In [ ]:
!pip install mlflow boto3 awscli optuna imbalanced-learn lightgbm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.7/24.7 MB 59.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 58.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.9/139.9 kB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 81.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.9/13.9 MB 96.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 395.9/395.9 kB 26.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 247.0/247.0 kB 18.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.8/147.8 kB 11.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 570.5/570.5 kB 37.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.9/114.9 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.0/85.0 kB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.3/85.3 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67

In [ ]:
from google.colab import userdata
import os

# Retrieve AWS credentials from Colab Secrets
aws_access_key = userdata.get('AWS_ACCESS_KEY_ID')
aws_secret_key = userdata.get('AWS_SECRET_ACCESS_KEY')
mlflow_uri = userdata.get('MLFLOW_TRACKING_URI')

# Set as environment variables (for boto3 and AWS CLI)
os.environ["AWS_ACCESS_KEY_ID"] = aws_access_key
os.environ["AWS_SECRET_ACCESS_KEY"] = aws_secret_key

In [ ]:
import mlflow
mlflow.set_tracking_uri(mlflow_uri)
mlflow.set_experiment("Exp 6 - lightbgm Detailed hpt")

2025/07/25 01:41:43 INFO mlflow.tracking.fluent: Experiment with name 'Exp 6 - lightbgm Detailed hpt' does not exist. Creating a new experiment.


<Experiment: artifact_location='s3://sumanthdatahub/mlflow-artifacts/141730004232532792', creation_time=1753407703605, experiment_id='141730004232532792', last_update_time=1753407703605, lifecycle_stage='active', name='Exp 6 - lightbgm Detailed hpt', tags={}>

In [ ]:
import optuna
import mlflow.sklearn
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, classification_report
from sklearn.feature_extraction.text import TfidfVectorizer
from lightgbm import LGBMClassifier
from imblearn.over_sampling import SMOTE
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd

In [ ]:
# Read Preprocesssing Data
df = pd.read_csv('/content/reddit_preprocessing.csv').dropna()
df.shape

(36710, 6)

In [ ]:
df['category'] = df['category'].map({-1: 2, 0: 0, 1: 1})
df = df.dropna(subset=['category'])

In [ ]:
ngram_range = (1,3)
max_features = 1000

vectorizer = TfidfVectorizer(ngram_range=ngram_range, max_features=max_features)
X = vectorizer.fit_transform(df['clean_comment'])
y = df['category']

smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42, stratify=y_resampled)

In [ ]:
def log_mlflow(model_name, model, X_train, X_test, y_train, y_test, params, trial_number):
    with mlflow.start_run():
        # Set Tags
        tags = {
            "mlflow.runName": f"Trial_{trial_number}_{model_name}_SMOTE_TFIDF_Trigrams",
            "experiment_type": "algorithm_comparison"
        }
        mlflow.set_tags(tags)

        # Log algorithm name as a parameter
        mlflow.log_param("algo_name", model_name)

        # Log hyperparameters
        for key, value in params.items():
            mlflow.log_param(key, value)

        # Train model
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)

        # Log accuracy
        accuracy = accuracy_score(y_test, y_pred)
        mlflow.log_metric("accuracy", accuracy)

        # Log classification report
        classification_rep = classification_report(y_test, y_pred, output_dict=True)
        for label, metrics in classification_rep.items():
            if isinstance(metrics, dict):
                for metric, value in metrics.items():
                    mlflow.log_metric(f"{label}_{metric}", value)

        # Log the model
        mlflow.sklearn.log_model(model, f"{model_name}_model")

        return accuracy

In [ ]:
# Optuna Objective function for LightGBM

def objective_lightgbm(trial):
    # Hyperparameter space to explore
    n_estimators = trial.suggest_int('n_estimators', 100, 1000)
    learning_rate = trial.suggest_float('learning_rate', 1e-4, 1e-1, log=True)
    max_depth = trial.suggest_int('max_depth', 3, 15)
    num_leaves = trial.suggest_int('num_leaves', 20, 150)
    min_child_samples = trial.suggest_int('min_child_samples', 10, 100)
    colsample_bytree = trial.suggest_float('colsample_bytree', 0.5, 1.0)
    subsample = trial.suggest_float('subsample', 0.5, 1.0)
    reg_alpha = trial.suggest_float('reg_alpha', 1e-4, 10.0, log=True)  # L1 regularization
    reg_lambda = trial.suggest_float('reg_lambda', 1e-4, 10.0, log=True)  # L2 regularization

    # Log trial parameters
    params = {
        'n_estimators': n_estimators,
        'learning_rate': learning_rate,
        'max_depth': max_depth,
        'num_leaves': num_leaves,
        'min_child_samples': min_child_samples,
        'colsample_bytree': colsample_bytree,
        'subsample': subsample,
        'reg_alpha': reg_alpha,
        'reg_lambda': reg_lambda
    }

    # Create LightGBM model
    model = LGBMClassifier(n_estimators=n_estimators,
                           learning_rate=learning_rate,
                           max_depth=max_depth,
                           num_leaves=num_leaves,
                           min_child_samples=min_child_samples,
                           colsample_bytree=colsample_bytree,
                           subsample=subsample,
                           reg_alpha=reg_alpha,
                           reg_lambda=reg_lambda,
                           random_state=42)

    # Log each trial as a separate run in MLflow
    accuracy = log_mlflow("LightGBM", model, X_train, X_test, y_train, y_test, params, trial.number)

    return accuracy

In [ ]:
def run_optuna_experiment():
    study = optuna.create_study(direction="maximize")
    study.optimize(objective_lightgbm, n_trials=100)  # Increased to 100 trials

    # Get the best parameters
    best_params = study.best_params
    best_model = LGBMClassifier(n_estimators=best_params['n_estimators'],
                                learning_rate=best_params['learning_rate'],
                                max_depth=best_params['max_depth'],
                                num_leaves=best_params['num_leaves'],
                                min_child_samples=best_params['min_child_samples'],
                                colsample_bytree=best_params['colsample_bytree'],
                                subsample=best_params['subsample'],
                                reg_alpha=best_params['reg_alpha'],
                                reg_lambda=best_params['reg_lambda'],
                                random_state=42)

    # Log the best model with MLflow and print the classification report
    log_mlflow("LightGBM", best_model, X_train, X_test, y_train, y_test, best_params, "Best")

    # Plot parameter importance
    optuna.visualization.plot_param_importances(study).show()

    # Plot optimization history
    optuna.visualization.plot_optimization_history(study).show()

In [ ]:
# Run the experiment for Lightgbm
run_optuna_experiment()

[I 2025-07-25 01:58:32,952] A new study created in memory with name: no-name-c927eb2e-d017-474f-8328-2ebcd703ec7d


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.259077 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 98798
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 959
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/07/25 01:58:41 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/07/25 01:58:52 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-07-25 01:58:53,708] Trial 0 finished with value: 0.5529486366518707 and parameters: {'n_estimators': 125, 'learning_rate': 0.001446142407520983, 'max_depth': 3, 'num_leaves': 130, 'min_child_samples': 59, 'colsample_bytree': 0.8266212658001035, 'subsample': 0.8704982039337059, 'reg_alpha': 0.6649747198248533, 'reg_lambda': 0.002152776495253034}. Best is trial 0 with value: 0.5529486366518707.


🏃 View run Trial_0_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-54-87-129-244.compute-1.amazonaws.com:5000/#/experiments/141730004232532792/runs/74e8d7e52f2b4ac791b7b3497beb549f
🧪 View experiment at: http://ec2-54-87-129-244.compute-1.amazonaws.com:5000/#/experiments/141730004232532792
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.276266 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 98928
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 966
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/07/25 02:00:11 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/07/25 02:00:20 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-07-25 02:00:21,664] Trial 1 finished with value: 0.8091312618896639 and parameters: {'n_estimators': 691, 'learning_rate': 0.026166892235457324, 'max_depth': 11, 'num_leaves': 62, 'min_child_samples': 51, 'colsample_bytree': 0.8764629132204174, 'subsample': 0.7589048629066306, 'reg_alpha': 0.0031489156809257316, 'reg_lambda': 0.0037603136443723215}. Best is trial 1 with value: 0.8091312618896639.


...

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/07/25 03:13:52 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/07/25 03:13:59 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-07-25 03:14:01,286] Trial 51 finished with value: 0.816423589093215 and parameters: {'n_estimators': 670, 'learning_rate': 0.051807566413016856, 'max_depth': 13, 'num_leaves': 105, 'min_child_samples': 28, 'colsample_bytree': 0.5056643893298637, 'subsample': 0.9987563595133558, 'reg_alpha': 0.03912677762452216, 'reg_lambda': 0.02253453185622527}. Best is trial 14 with value: 0.8207567110547453.


🏃 View run Trial_51_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-54-87-129-244.compute-1.amazonaws.com:5000/#/experiments/141730004232532792/runs/fd7409dccb124364b5d1d0c5009d99fd
🧪 View experiment at: http://ec2-54-87-129-244.compute-1.amazonaws.com:5000/#/experiments/141730004232532792
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.466291 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 98950
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 968
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/07/25 03:16:05 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/07/25 03:16:13 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-07-25 03:16:14,432] Trial 52 finished with value: 0.8169520186007186 and parameters: {'n_estimators': 717, 'learning_rate': 0.08131885779828495, 'max_depth': 12, 'num_leaves': 106, 'min_child_samples': 25, 'colsample_bytree': 0.5313661840447244, 'subsample': 0.973870486192127, 'reg_alpha': 0.024011360438411355, 'reg_lambda': 0.07206470590780177}. Best is trial 14 with value: 0.8207567110547453.


🏃 View run Trial_52_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-54-87-129-244.compute-1.amazonaws.com:5000/#/experiments/141730004232532792/runs/e6c1050e037f42adbffa85728f3a2504
🧪 View experiment at: http://ec2-54-87-129-244.compute-1.amazonaws.com:5000/#/experiments/141730004232532792
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.262646 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 98928
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 966
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with p

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/07/25 03:17:47 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
